## **The Mile Approch** 

**This post office serves a radius of 5 kilometers, encompassing 2500 delivery points. It employs a team of 20 delivery personnel**
* 2500 delivery points 
* 20 delivery personnel
* 4 km Radius 

### **Step 1 : Plot Delivery Locations**

In [2]:
import numpy as np

# Central point (latitude and longitude) for Bengaluru
center_lat = 12.9716
center_lon = 77.5946

# Function to generate random points within a given radius
def generate_random_points(center_lat, center_lon, radius_km, num_points):
    # Earth's radius in kilometers
    earth_radius_km = 6371.0
    
    # Convert radius from km to radians
    radius_radians = radius_km / earth_radius_km

    points = []
    for _ in range(num_points):
        # Random distance from the center within the specified radius
        distance = np.random.uniform(0, radius_radians)

        # Random angle between 0 and 360 degrees (in radians)
        angle = np.random.uniform(0, 2 * np.pi)

        # New latitude and longitude using the Haversine formula
        new_lat = np.arcsin(np.sin(np.radians(center_lat)) * np.cos(distance) +
                            np.cos(np.radians(center_lat)) * np.sin(distance) * np.cos(angle))
        new_lon = np.radians(center_lon) + np.arctan2(np.sin(angle) * np.sin(distance) * np.cos(np.radians(center_lat)),
                                                      np.cos(distance) - np.sin(np.radians(center_lat)) * np.sin(new_lat))

        # Convert back to degrees
        new_lat = np.degrees(new_lat)
        new_lon = np.degrees(new_lon)

        points.append((new_lat, new_lon))

    return points

# Generate 2500 random points within 5 km radius
num_points = 2500
radius_km = 5
points = generate_random_points(center_lat, center_lon, radius_km, num_points)

# Save the points in an array
points_array = np.array(points)

# Output the array
print(points_array)


[[12.96109074 77.59231362]
 [12.9869014  77.61029982]
 [12.97134866 77.59034681]
 ...
 [12.94168679 77.60003903]
 [12.95926169 77.58834616]
 [12.97549129 77.61274338]]


* The `points_array` contains the geographic coordinates (latitude and longitude) of all delivery locations.

## **Step 2 : Assign Drivers**

* The 2500 delivery points are divided into 20 clusters to match the number of delivery personnel, with 20 personnel available in this case. The number of clusters can be adjusted as needed, depending on staffing availability

In [7]:
import numpy as np
from sklearn.cluster import KMeans
import folium

# Central point (latitude and longitude) for Bengaluru
center_lat = 12.9716
center_lon = 77.5946

# Function to generate random points within a given radius
def generate_random_points(center_lat, center_lon, radius_km, num_points):
    earth_radius_km = 6371.0
    radius_radians = radius_km / earth_radius_km
    points = []
    
    for _ in range(num_points):
        distance = np.random.uniform(0, radius_radians)
        angle = np.random.uniform(0, 2 * np.pi)
        new_lat = np.arcsin(np.sin(np.radians(center_lat)) * np.cos(distance) +
                            np.cos(np.radians(center_lat)) * np.sin(distance) * np.cos(angle))
        new_lon = np.radians(center_lon) + np.arctan2(np.sin(angle) * np.sin(distance) * np.cos(np.radians(center_lat)),
                                                      np.cos(distance) - np.sin(np.radians(center_lat)) * np.sin(new_lat))
        points.append((np.degrees(new_lat), np.degrees(new_lon)))

    return points

# Generate 2500 random points within a 5 km radius
num_points = 2500
radius_km = 5
points = generate_random_points(center_lat, center_lon, radius_km, num_points)
points_array = np.array(points)

# Apply K-Means clustering to divide the points into 20 clusters
num_clusters = 20
kmeans = KMeans(n_clusters=num_clusters, random_state=42)
kmeans.fit(points_array)
labels = kmeans.labels_  # Cluster labels for each point

# Define 20 unique colors for the clusters
colors = [
    'red', 'blue', 'green', 'purple', 'orange', 'darkred', 'lightred',
    'beige', 'darkblue', 'darkgreen', 'cadetblue', 'lightgreen', 'gray',
    'black', 'lightgray', 'pink', 'lightblue', 'lightgray', 'white', 'darkpurple'
]

# Count the number of points in each cluster and print it with the assigned color
cluster_counts = np.bincount(labels)
for cluster_id, count in enumerate(cluster_counts):
    color = colors[cluster_id % num_clusters]
    print(f"Cluster {cluster_id + 1} ({color}): {count} points")

# Create a map centered at the central point in Bengaluru
central_point = [center_lat, center_lon]
m = folium.Map(location=central_point, tiles="cartodbpositron", zoom_start=14)

# Add markers for each point with a different color based on its cluster
for i, coord in enumerate(points_array):
    cluster_id = labels[i]
    color = colors[cluster_id % num_clusters]  # Assign a color based on the cluster
    folium.CircleMarker(
        location=[coord[0], coord[1]],
        radius=3,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.6,
        popup=f"Cluster {cluster_id + 1}"
    ).add_to(m)

# Display the map
m


Cluster 1 (red): 166 points
Cluster 2 (blue): 92 points
Cluster 3 (green): 105 points
Cluster 4 (purple): 80 points
Cluster 5 (orange): 156 points
Cluster 6 (darkred): 79 points
Cluster 7 (lightred): 130 points
Cluster 8 (beige): 77 points
Cluster 9 (darkblue): 144 points
Cluster 10 (darkgreen): 97 points
Cluster 11 (cadetblue): 101 points
Cluster 12 (lightgreen): 135 points
Cluster 13 (gray): 101 points
Cluster 14 (black): 393 points
Cluster 15 (lightgray): 97 points
Cluster 16 (pink): 60 points
Cluster 17 (lightblue): 85 points
Cluster 18 (lightgray): 111 points
Cluster 19 (white): 138 points
Cluster 20 (darkpurple): 153 points


## **Step 3 : Focus on One Driver's Deliveries**

* To simplify our analysis, let's focus on a single driver and examine the operations of one delivery cluster.

In [45]:
import numpy as np
from sklearn.cluster import KMeans
import folium

# Central point (latitude and longitude) for Bengaluru
center_lat = 12.9716
center_lon = 77.5946

# Function to generate random points within a given radius
def generate_random_points(center_lat, center_lon, radius_km, num_points):
    earth_radius_km = 6371.0
    radius_radians = radius_km / earth_radius_km
    points = []

    for _ in range(num_points):
        distance = np.random.uniform(0, radius_radians)
        angle = np.random.uniform(0, 2 * np.pi)
        new_lat = np.arcsin(np.sin(np.radians(center_lat)) * np.cos(distance) +
                            np.cos(np.radians(center_lat)) * np.sin(distance) * np.cos(angle))
        new_lon = np.radians(center_lon) + np.arctan2(np.sin(angle) * np.sin(distance) * np.cos(np.radians(center_lat)),
                                                      np.cos(distance) - np.sin(np.radians(center_lat)) * np.sin(new_lat))
        points.append((np.degrees(new_lat), np.degrees(new_lon)))

    return points

# Generate 2500 random points within a 5 km radius
num_points = 2500
radius_km = 5
points = generate_random_points(center_lat, center_lon, radius_km, num_points)
points_array = np.array(points)

# Apply K-Means clustering to divide the points into 20 clusters
num_clusters = 20
kmeans = KMeans(n_clusters=num_clusters, random_state=42)
kmeans.fit(points_array)
labels = kmeans.labels_  # Cluster labels for each point

# Define 20 unique colors for the clusters
colors = [
    'red', 'blue', 'green', 'purple', 'orange', 'darkred', 'lightred',
    '', 'darkblue', 'darkgreen', 'cadetblue', 'lightgreen', '',
    'black', '', 'pink', 'lightblue', '', '', 'darkpurple'
]

# Select the cluster you want to plot (in this case, cluster 8)
cluster_to_plot = 7  # (since the cluster index starts from 0, 8th cluster is index 7)
color_for_cluster = colors[cluster_to_plot % num_clusters]

# Get all the points that belong to the 8th cluster
cluster_points = points_array[labels == cluster_to_plot]

# Print the coordinates of all points in the 18th cluster
print(f"Coordinates of all points in Cluster 18 ({color_for_cluster}):")
for point in cluster_points:
    print(f"Latitude: {point[0]}, Longitude: {point[1]}")

# Create a map centered at the central point in Bengaluru
central_point = [center_lat, center_lon]
m = folium.Map(location=central_point, tiles="cartodbpositron", zoom_start=14)

# Plot the central point with a distinctive marker
folium.Marker(
    location=central_point,
    popup="Central Point (Bengaluru)",
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Add markers for each point in the selected cluster
for coord in cluster_points:
    folium.CircleMarker(
        location=[coord[0], coord[1]],
        radius=3,
        color=color_for_cluster,
        fill=True,
        fill_color=color_for_cluster,
        fill_opacity=0.6,
        popup=f"Cluster 18<br>Lat: {coord[0]:.6f}, Long: {coord[1]:.6f}"
    ).add_to(m)

# Display the map
m

Coordinates of all points in Cluster 18 ():
Latitude: 12.944283458819369, Longitude: 77.59556068472642
Latitude: 12.942743195709438, Longitude: 77.5857635655806
Latitude: 12.941210816072626, Longitude: 77.5840043138582
Latitude: 12.938260932209099, Longitude: 77.58980423459258
Latitude: 12.933654170196082, Longitude: 77.59310358627789
Latitude: 12.941618333815029, Longitude: 77.58814880181566
Latitude: 12.933295435752656, Longitude: 77.58763616318944
Latitude: 12.945244718922337, Longitude: 77.59707307492899
Latitude: 12.940834517181608, Longitude: 77.58370537193994
Latitude: 12.935393004582465, Longitude: 77.59757798705027
Latitude: 12.940569758875366, Longitude: 77.58082875809868
Latitude: 12.932330404779643, Longitude: 77.58022439521024
Latitude: 12.938898943402936, Longitude: 77.59174053447116
Latitude: 12.931258791018026, Longitude: 77.58461579417295
Latitude: 12.93996314960484, Longitude: 77.58771432408736
Latitude: 12.933484805341813, Longitude: 77.58768274038242
Latitude: 12.93

* This delivery cluster consists of 92 total delivery points

## **Step 4 : Time concept**

#### Daily Target and Average Delivery Time

* **Daily Target:** The primary goal for each driver is to deliver 92 items during the 8 time-slots. `(92 deliveries / 8 time slots = 11.5 deliveries per slot)`
* **Average Delivery Time:** To meet this target, drivers must maintain a consistent pace, completing approximately 11-12 deliveries per hour `(60 minutes / 12 = 5 minutes)`. This translates to just under 5 minutes per delivery, which requires efficient planning and execution.

#### Time Slot Allocation and Constraints

* **Time Slot Allocation:** The system plays a crucial role in assigning time slots to customers. It considers the travel time between delivery points to ensure that drivers can reach their destinations within the allotted time.
* **Time Slot Constraints:** When a customer (Person A) selects a time slot, the system evaluates whether another customer (Person B) can choose the same slot based on the travel time between their locations. If Person B’s travel time from Person A’s location is less than ***5 minutes + Buffer Time***, they can book the same slot; otherwise, they cannot. This ensures drivers can meet their delivery schedules without delays

#### Buffer Time

* **Unforeseen Delays:** Delivery operations are subject to various uncertainties, such as traffic congestion, weather conditions, or unexpected delays at customer locations.
* **Buffer Time:** To accommodate these potential disruptions, a buffer time of 1-2 minutes is incorporated into the schedule. This extra time provides flexibility, allowing drivers to handle unforeseen circumstances without compromising their overall efficiency.

<div class="alert alert-block alert-info">
<b>Note:</b> This step typically occurs on the mobile application or on the website, where users are presented with available time slots. The underlying model or algorithm dynamically evaluates each selection, accepting or rejecting it based on real-time factors such as travel times and scheduling constraints. 
</div>

In [47]:
import random
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
import time

# List of all delivery points (latitude, longitude)
delivery_points = [
(12.944283458819369,  77.59556068472642),
(12.942743195709438,  77.5857635655806),
(12.941210816072626,  77.5840043138582),
(12.938260932209099,  77.58980423459258),
(12.933654170196082,  77.59310358627789),
(12.941618333815029,  77.58814880181566),
(12.933295435752656,  77.58763616318944),
(12.945244718922337,  77.59707307492899),
(12.940834517181608,  77.58370537193994),
(12.935393004582465,  77.59757798705027),
(12.940569758875366,  77.58082875809868),
(12.932330404779643,  77.58022439521024),
(12.938898943402936,  77.59174053447116),
(12.931258791018026,  77.58461579417295),
(12.93996314960484,  77.58771432408736),
(12.933484805341813,  77.58768274038242),
(12.934195827890774,  77.5901776403424),
(12.939910470129721,  77.58959853115942),
(12.942916289790018,  77.592291653484),
(12.942182599162008,  77.595396131983),
(12.938553189539554,  77.58293474580447),
(12.929186334425701,  77.5961026301268),
(12.931496523749868,  77.57441157547197),
(12.927658635137112,  77.59065541499486),
(12.929755137041624,  77.592394400121),
(12.937549930857328,  77.58953595428258),
(12.928928725727461,  77.5923705091729),
(12.93654014065685,  77.58313926857798),
(12.938454549651526,  77.58549622792468),
(12.941169433543534,  77.59072390573513),
(12.937380143751376,  77.57767305458246),
(12.936280590482971,  77.59015206538778),
(12.94325900104295,  77.58697660509144),
(12.94050934547309,  77.58134541584282),
(12.927477112973193,  77.5890161675519),
(12.92679096527194,  77.59426386727272),
(12.937339115354831,  77.59191370277102),
(12.944462657617375,  77.58938626299225),
(12.94169209094121,  77.58174966765053),
(12.940110892221757,  77.58771292795456),
(12.944867546427943,  77.59007861023119),
(12.932058700934766,  77.58515688501973),
(12.93259592723351,  77.58013663460522),
(12.940869854364115,  77.58423666867404),
(12.934412802841111,  77.5750957349543),
(12.928767498285646,  77.59488945772341),
(12.928537892794768,  77.58830149750285),
(12.93010873363301,  77.59413549741602),
(12.927250525447617,  77.59785371140373),
(12.930098921283676,  77.58956372882166),
(12.943230697241166,  77.58798663940652),
(12.938790519902957,  77.58168913279246),
(12.930758865165766,  77.5839943687262),
(12.939032107658473,  77.58907754911165),
(12.941724954757921,  77.58587458694103),
(12.942050955307755,  77.59268351532383),
(12.935297584268392,  77.57551824110854),
(12.936331465401226,  77.59709895210737),
(12.94203407467455,  77.597025241049),
(12.929654407412784,  77.58474561430903),
(12.931883090447325,  77.58700424557559),
(12.942976932022475,  77.59387500059823),
(12.943517758326474,  77.59452976448515),
(12.942240713009465,  77.59000054070701),
(12.94765917222878,  77.59001524756545),
(12.935496586668005,  77.58449234049542),
(12.934237499195442,  77.5837673495615),
(12.93681753712716,  77.57706535180128),
(12.941560605713377,  77.58966290160355),
(12.94421214365001,  77.58722865688672),
(12.932270765041482,  77.57238685868671),
(12.943524288579429,  77.59291715555352),
(12.94259753591173,  77.58948878223995),
(12.940351441215675,  77.58142003096776),
(12.94253038072308,  77.58918296812668),
(12.940110844856374,  77.58898408050848),
(12.945029169025275,  77.59270793284941),
(12.930809892928677,  77.58372213236689),
(12.938328781523722,  77.59706120047242),
(12.940441704776731,  77.58260699859765),
(12.933508382005801,  77.58687468225703),
(12.93622842327097,  77.58264288586348),
(12.930664343773785,  77.58025865809648),
(12.929862759311606,  77.581035597506),
(12.931149603820739,  77.59787662350584),
(12.93620852829792,  77.5901752740488),
(12.947004905051179,  77.58861160548493),
(12.937672530173884,  77.59215523387832),
(12.939568404895432,  77.58619417000622),
(12.938806086191653,  77.59319418077574),
(12.94564978520275,  77.59169733260846),
(12.945721121989441,  77.5964320606102)
]

# Time slots
time_slots = ['9-10', '10-11', '11-12', '12-1', '2-3', '3-4', '4-5', '5-6']

# Shuffle the delivery points randomly
random.shuffle(delivery_points)

# Create a list to store the deliveries for each time slot
deliveries_by_time_slot = {slot: [] for slot in time_slots}

# Initialize webdriver for scraping Google Maps (make sure to use the correct driver for your browser)
def generate_google_maps_links(start, end):
    base_url = "https://www.google.com/maps/dir/"
    link = f"{base_url}{start[0]},{start[1]}/{end[0]},{end[1]}/"
    return link

def scrape_travel_time(driver, link):
    driver.get(link)
    try:
        element = WebDriverWait(driver, 10).until(
            EC.presence_of_element_located((By.CLASS_NAME, "Fl2iee"))
        )
        time_elements = driver.find_elements(By.CLASS_NAME, "Fl2iee")
        travel_times = [elem.text for elem in time_elements]
        
        # Find a valid time value like "6 min", and ignore non-numeric text like "Best"
        for time_text in travel_times:
            if "min" in time_text:
                # Extract the number from the string
                time_number = time_text.split()[0]
                if time_number.isdigit():
                    return int(time_number)
        
        return None  # Return None if no valid time is found
    except TimeoutException:
        return None

def process_delivery_slots(delivery_points, time_slots):
    driver = webdriver.Firefox()  # Make sure you have the correct geckodriver installed
    slot_time_limits = {slot: 0 for slot in time_slots}  # Track total time in each slot
    slot_index = 0  # Start with the first slot

    for i in range(len(delivery_points)):
        start = delivery_points[i - 1] if i > 0 else None
        end = delivery_points[i]

        # If it's the first point, just place it in the current slot
        if i == 0:
            deliveries_by_time_slot[time_slots[slot_index]].append(end)
            print(f"First point {end} placed in time slot '{time_slots[slot_index]}'")
            continue

        # Get the travel time between consecutive points
        if start:
            link = generate_google_maps_links(start, end)
            travel_time_minutes = scrape_travel_time(driver, link)

            if travel_time_minutes is None:
                print(f"Could not retrieve valid time for link: {link}")
                continue

            # Try to place the delivery in the current slot, else try the next slot
            placed = False
            while not placed:
                # Check if the current slot can accommodate this delivery
                if travel_time_minutes <= 7 and slot_time_limits[time_slots[slot_index]] + travel_time_minutes <= 60:
                    deliveries_by_time_slot[time_slots[slot_index]].append(end)
                    slot_time_limits[time_slots[slot_index]] += travel_time_minutes
                    placed = True

                    # Display the time between points and the updated total time in the slot
                    print(f"Time between points {start} and {end}: {travel_time_minutes} minutes")
                    print(f"Total time in current slot '{time_slots[slot_index]}': {slot_time_limits[time_slots[slot_index]]} minutes")
                else:
                    # Move to the next slot
                    print(f"Cannot place point {end} in time slot '{time_slots[slot_index]}'")
                    slot_index = (slot_index + 1) % len(time_slots)  # Cycle through the time slots

                    # If we've looped back to the beginning and still can't place the point, break the loop
                    if slot_index == 0:
                        print("All time slots are full or cannot accommodate the remaining points!")
                        break

        # Add a small delay between requests
        time.sleep(2)

    driver.quit()
    return deliveries_by_time_slot

# Process and assign delivery points to time slots
delivery_schedule = process_delivery_slots(delivery_points, time_slots)

# Output the result
print("\nFinal Delivery Schedule:")
for slot, deliveries in delivery_schedule.items():
    print(f"Time Slot: {slot} -> {len(deliveries)} deliveries")
    for delivery in deliveries:
        print(delivery)
    print()


First point (12.937672530173884, 77.59215523387832) placed in time slot '9-10'
Time between points (12.937672530173884, 77.59215523387832) and (12.928767498285646, 77.59488945772341): 6 minutes
Total time in current slot '9-10': 6 minutes
Time between points (12.928767498285646, 77.59488945772341) and (12.938806086191653, 77.59319418077574): 7 minutes
Total time in current slot '9-10': 13 minutes
Time between points (12.938806086191653, 77.59319418077574) and (12.92679096527194, 77.59426386727272): 5 minutes
Total time in current slot '9-10': 18 minutes
Cannot place point (12.937380143751376, 77.57767305458246) in time slot '9-10'
Cannot place point (12.937380143751376, 77.57767305458246) in time slot '10-11'
Cannot place point (12.937380143751376, 77.57767305458246) in time slot '11-12'
Cannot place point (12.937380143751376, 77.57767305458246) in time slot '12-1'
Cannot place point (12.937380143751376, 77.57767305458246) in time slot '2-3'
Cannot place point (12.937380143751376, 77.5

<div style="background-color:#e6ffe6; color:green; padding:15px; border-radius:10px; border:1px solid #d4f2d4; font-family:Arial, sans-serif; font-size:14px;">
    
<h4 style="color:red"><b>Note: This process typically occurs on the front-end, where users have full control over selecting their preferred time slots. However, we are using this code for a simplified purpose: classifying coordinate points</h2>
    <ol>
        <li>Takes a list of delivery locations in Bangalore (the coordinates are in that area)<b></li>
        <li>Divides the working day into 8 time slots (like 9-10 AM, 10-11 AM, etc.)</li>
        <li>Uses Google Maps to check how long it takes to drive between each location</li>
        <li>Creates a delivery schedule following these rules:
            <ul>
                <li>No more than 7 minutes travel time between stops</li>
                <li>No more than 60 minutes total work per time slot</li>
                <li>Tries to group nearby deliveries in the same time slot</li>
            </ul>
        </li>
    </ol>
</div>


In [49]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
import time

def generate_google_maps_links(coordinates):
    links = []
    base_url = "https://www.google.com/maps/dir/"
    
    for i in range(len(coordinates) - 1):
        start = coordinates[i]
        end = coordinates[i + 1]
        
        # Generate the link for each consecutive pair of points
        link = f"{base_url}{start[0]},{start[1]}/{end[0]},{end[1]}/"
        links.append(link)
    
    return links

def scrape_google_maps_data(links):
    # Initialize the webdriver (you'll need to download the appropriate driver for your browser)
    # driver = webdriver.Chrome()  # or webdriver.Firefox(), etc.
    driver = webdriver.Firefox()  # Make sure to have the correct geckodriver installed
    
    results = []
    
    for link in links:
        driver.get(link)
        
        try:
            # Wait for the element to be present (adjust the timeout as needed)
            element = WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.CLASS_NAME, "Fl2iee"))
            )
            
            # Find all elements with class "Fl2iee"
            time_elements = driver.find_elements(By.CLASS_NAME, "Fl2iee")
            
            # Extract the text from these elements
            times = [elem.text for elem in time_elements]
            
            results.append(times)
            
            # Add a delay to avoid overwhelming the server
            time.sleep(2)
            
        except TimeoutException:
            print(f"Timed out waiting for page to load: {link}")
            results.append(None)
    
    driver.quit()
    return results

# Example list of coordinates
coordinates = [

(12.937672530173884, 77.59215523387832),
(12.928767498285646, 77.59488945772341),
(12.938806086191653, 77.59319418077574),
(12.92679096527194, 77.59426386727272),
(12.938898943402936, 77.59174053447116),
(12.941618333815029, 77.58814880181566),
(12.928537892794768, 77.58830149750285),
(12.929862759311606, 77.581035597506),
(12.940869854364115, 77.58423666867404),
(12.929654407412784, 77.58474561430903),
(12.928928725727461, 77.5923705091729),
(12.94325900104295, 77.58697660509144),

]

# Generate the Google Maps links
links = generate_google_maps_links(coordinates)

# Print the generated links
print("Generated Links:")
for i, link in enumerate(links):
    print(f"Link for stop {i+1} and stop {i+2}: {link}")

# Scrape data from the generated links
print("\nScraping data from links...")
scraped_data = scrape_google_maps_data(links)

# Print the scraped results
print("\nScraped Data:")
for i, data in enumerate(scraped_data):
    print(f"Data for link {i+1}: {data}")

# Extract the third column (e.g., '6 min') from the scraped data for each link
print("\nExtracted Third Column Data:")
for i, data in enumerate(scraped_data):
    if data and len(data) > 2:  # Check if there is enough data
        third_column = data[2]  # Extract the third element (index 2)
        print(f"Time by motor bike for link {i+1}: {third_column}")
    else:
        print(f"Not enough data for link {i+1}")


Generated Links:
Link for stop 1 and stop 2: https://www.google.com/maps/dir/12.937672530173884,77.59215523387832/12.928767498285646,77.59488945772341/
Link for stop 2 and stop 3: https://www.google.com/maps/dir/12.928767498285646,77.59488945772341/12.938806086191653,77.59319418077574/
Link for stop 3 and stop 4: https://www.google.com/maps/dir/12.938806086191653,77.59319418077574/12.92679096527194,77.59426386727272/
Link for stop 4 and stop 5: https://www.google.com/maps/dir/12.92679096527194,77.59426386727272/12.938898943402936,77.59174053447116/
Link for stop 5 and stop 6: https://www.google.com/maps/dir/12.938898943402936,77.59174053447116/12.941618333815029,77.58814880181566/
Link for stop 6 and stop 7: https://www.google.com/maps/dir/12.941618333815029,77.58814880181566/12.928537892794768,77.58830149750285/
Link for stop 7 and stop 8: https://www.google.com/maps/dir/12.928537892794768,77.58830149750285/12.929862759311606,77.581035597506/
Link for stop 8 and stop 9: https://www.go

* The code above can be used to calculate the travel time between two locations

## **Step 5 : Route Optimization**

* Let's optimize the delivery route for the following coordinate points within the time slot of 9:00 AM to 10:00 AM


In [52]:
import openrouteservice
import folium
from openrouteservice.optimization import Vehicle, Job
import numpy as np

# Your OpenRouteService API Key
api_key = '5b3ce3597851110001cf62482f55acfcd7a2475c84a061e54824b8d6'

# Initialize the client
client = openrouteservice.Client(key=api_key)

# Define the coordinates
coordinates = [
(12.937672530173884, 77.59215523387832),
(12.928767498285646, 77.59488945772341),
(12.938806086191653, 77.59319418077574),
(12.92679096527194, 77.59426386727272),
(12.938898943402936, 77.59174053447116),
(12.941618333815029, 77.58814880181566),
(12.928537892794768, 77.58830149750285),
(12.929862759311606, 77.581035597506),
(12.940869854364115, 77.58423666867404),
(12.929654407412784, 77.58474561430903),
(12.928928725727461, 77.5923705091729),
(12.94325900104295, 77.58697660509144),


]

# Convert coordinates to the format required by OpenRouteService (lon, lat)
coordinates_ors = [(coord[1], coord[0]) for coord in coordinates]  # ORS expects (lon, lat)

# Define the vehicle and job objects for the optimization process
jobs = [Job(id=i, location=coord) for i, coord in enumerate(coordinates_ors)]
vehicles = [Vehicle(id=1, profile='driving-car', start=coordinates_ors[0], end=coordinates_ors[0])]

try:
    # Try to calculate an optimized route (Traveling Salesman Problem)
    optimized_route = client.optimization(
        jobs=jobs,
        vehicles=vehicles
    )
except openrouteservice.exceptions.ApiError as e:
    print("Error during initial optimization:", str(e))

    # If there is an error with a specific location, handle it by finding the nearest point
    if 'Unfound route' in str(e):
        print("Route not found for a location, finding nearest available point.")
        
        # Use OpenRouteService's matrix API to get the distances between points
        matrix = client.distance_matrix(
            locations=coordinates_ors,
            profile='driving-car',
            metrics=['distance'],
        )
        
        # Find the nearest point with a valid route (ignoring the failing point)
        distance_matrix = np.array(matrix['distances'])
        np.fill_diagonal(distance_matrix, np.inf)  # Avoid self-comparison (distance to self is zero)

        # Find the nearest deliverable point for each failed location
        nearest_points = np.argmin(distance_matrix, axis=1)  # Get index of the nearest point

        # Reconstruct job list by replacing undeliverable points with nearest deliverable ones
        new_jobs = []
        for i, job in enumerate(jobs):
            nearest_point = coordinates_ors[nearest_points[i]]
            new_jobs.append(Job(id=i, location=nearest_point))

        # Re-run the optimization with adjusted locations
        optimized_route = client.optimization(
            jobs=new_jobs,
            vehicles=vehicles
        )

# Extract the optimized route coordinates and order
optimized_coordinates = []
optimized_order = []
for step in optimized_route['routes'][0]['steps']:
    if 'job' in step:
        optimized_coordinates.append(step['location'])
        optimized_order.append(step['job'])

# Create a map centered on the first point
map_center = [coordinates[0][0], coordinates[0][1]]
route_map = folium.Map(location=map_center, zoom_start=13)

# Add numbered markers to the map
for i, coord in enumerate(optimized_coordinates):
    folium.Marker(
        location=[coord[1], coord[0]],
        icon=folium.DivIcon(html=f'<div style="font-size: 12pt; color : black">{optimized_order[i] + 1}</div>'),
    ).add_to(route_map)

# Add the optimized route to the map
folium.PolyLine(locations=[(coord[1], coord[0]) for coord in optimized_coordinates],
                color="blue", weight=2.5, opacity=1).add_to(route_map)


route_map

## Step 6 : Special condition 

**In high-density delivery areas, like apartments or busy streets, we limit the number of available time slots to reduce travel time and fuel costs. Here's the strategy:**
* Identify high-density locations (e.g., many deliveries in one building or street).
* Restrict time slots for these locations, offering fewer options (e.g., 3 slots instead of 8).
* Group deliveries in the same area within these limited time slots, allowing the driver to deliver multiple packages in one trip.
* Optimize routes to reduce back-and-forth travel, saving time and fuel.
* Communicate clearly to users that time slots are limited due to high delivery volumes in their area.

In [38]:
import numpy as np
from sklearn.cluster import KMeans
import folium
from folium.plugins import HeatMap

# Central point (latitude and longitude) for Bengaluru
center_lat, center_lon = 12.9716, 77.5946

def generate_random_points(center_lat, center_lon, radius_km, num_points):
    earth_radius_km = 6371.0
    radius_radians = radius_km / earth_radius_km
    points = []

    for _ in range(num_points):
        distance = np.random.uniform(0, radius_radians)
        angle = np.random.uniform(0, 2 * np.pi)
        new_lat = np.arcsin(np.sin(np.radians(center_lat)) * np.cos(distance) +
                            np.cos(np.radians(center_lat)) * np.sin(distance) * np.cos(angle))
        new_lon = np.radians(center_lon) + np.arctan2(np.sin(angle) * np.sin(distance) * np.cos(np.radians(center_lat)),
                                                      np.cos(distance) - np.sin(np.radians(center_lat)) * np.sin(new_lat))
        points.append((np.degrees(new_lat), np.degrees(new_lon)))

    return points

# Generate points
num_points = 2500
radius_km = 5
points = generate_random_points(center_lat, center_lon, radius_km, num_points)
points_array = np.array(points)

# Create a grid
grid_size = 20
lat_bins = np.linspace(points_array[:, 0].min(), points_array[:, 0].max(), grid_size)
lon_bins = np.linspace(points_array[:, 1].min(), points_array[:, 1].max(), grid_size)

# Compute point density in each grid cell
H, _, _ = np.histogram2d(points_array[:, 0], points_array[:, 1], bins=[lat_bins, lon_bins])

# Find high-density areas (e.g., top 10% of density)
threshold = np.percentile(H, 90)
high_density_indices = np.where(H >= threshold)

# Get coordinates of high-density areas
high_density_coords = []
for i, j in zip(*high_density_indices):
    lat = (lat_bins[i] + lat_bins[i+1]) / 2
    lon = (lon_bins[j] + lon_bins[j+1]) / 2
    density = H[i, j]
    high_density_coords.append((lat, lon, density))

# Sort high-density coordinates by density (highest first)
high_density_coords.sort(key=lambda x: x[2], reverse=True)

# Print high-density coordinates
print("High-density area coordinates (Latitude, Longitude, Density):")
for lat, lon, density in high_density_coords:
    print(f"Lat: {lat:.6f}, Lon: {lon:.6f}, Density: {density}")

# Create a map
m = folium.Map(location=[center_lat, center_lon], zoom_start=13)

# Add a heat map layer
heat_data = [[point[0], point[1]] for point in points_array]
HeatMap(heat_data).add_to(m)

# Add markers for high-density areas
for lat, lon, density in high_density_coords:
    folium.CircleMarker(
        location=[lat, lon],
        radius=5,
        popup=f"Density: {density:.0f}",
        color="red",
        fill=True,
        fill_color="red"
    ).add_to(m)

# Display the map
m

High-density area coordinates (Latitude, Longitude, Density):
Lat: 12.971552, Lon: 77.594369, Density: 151.0
Lat: 12.971552, Lon: 77.599185, Density: 58.0
Lat: 12.971552, Lon: 77.589553, Density: 49.0
Lat: 12.976262, Lon: 77.594369, Density: 46.0
Lat: 12.966842, Lon: 77.594369, Density: 37.0
Lat: 12.966842, Lon: 77.589553, Density: 34.0
Lat: 12.971552, Lon: 77.604001, Density: 29.0
Lat: 12.976262, Lon: 77.599185, Density: 28.0
Lat: 12.966842, Lon: 77.599185, Density: 26.0
Lat: 12.962132, Lon: 77.594369, Density: 23.0
Lat: 12.980973, Lon: 77.589553, Density: 23.0
Lat: 12.980973, Lon: 77.599185, Density: 23.0
Lat: 12.990393, Lon: 77.599185, Density: 23.0
Lat: 12.976262, Lon: 77.589553, Density: 20.0
Lat: 12.966842, Lon: 77.579921, Density: 19.0
Lat: 12.971552, Lon: 77.608817, Density: 19.0
Lat: 12.980973, Lon: 77.584737, Density: 19.0
Lat: 12.985683, Lon: 77.599185, Density: 19.0
Lat: 12.985683, Lon: 77.604001, Density: 19.0
Lat: 12.976262, Lon: 77.584737, Density: 18.0
Lat: 12.976262, L

In [54]:
import numpy as np
from sklearn.cluster import DBSCAN
import folium
from geopy.distance import great_circle

# Central point (latitude and longitude) for Bengaluru
center_lat = 12.9716
center_lon = 77.5946

# Function to generate random points within a given radius
def generate_random_points(center_lat, center_lon, radius_km, num_points):
    earth_radius_km = 6371.0
    radius_radians = radius_km / earth_radius_km
    points = []

    for _ in range(num_points):
        distance = np.random.uniform(0, radius_radians)
        angle = np.random.uniform(0, 2 * np.pi)
        new_lat = np.arcsin(np.sin(np.radians(center_lat)) * np.cos(distance) +
                            np.cos(np.radians(center_lat)) * np.sin(distance) * np.cos(angle))
        new_lon = np.radians(center_lon) + np.arctan2(np.sin(angle) * np.sin(distance) * np.cos(np.radians(center_lat)),
                                                      np.cos(distance) - np.sin(np.radians(center_lat)) * np.sin(new_lat))
        points.append((np.degrees(new_lat), np.degrees(new_lon)))

    return points

# Generate 2500 random points within a 5 km radius
num_points = 2500
radius_km = 5
points = generate_random_points(center_lat, center_lon, radius_km, num_points)
points_array = np.array(points)

# DBSCAN parameters
eps_km = 0.3  # Maximum distance between two points for them to be considered in the same neighborhood (in kilometers)
min_samples = 10  # Minimum number of points to form a dense region (i.e., a cluster)

# Convert the geographical coordinates to distances for DBSCAN
dbscan = DBSCAN(eps=eps_km / 6371.0, min_samples=min_samples, algorithm='ball_tree', metric='haversine')

# Apply DBSCAN clustering
labels = dbscan.fit_predict(np.radians(points_array))

# Get unique clusters (-1 indicates noise points)
unique_labels = set(labels)

# Define colors for clusters (randomly assigned)
colors = [
    'red', 'blue', 'green', 'purple', 'orange', 'darkred', 'lightred',
    'beige', 'darkblue', 'darkgreen', 'cadetblue', 'lightgreen', 'black',
    'pink', 'lightblue', 'gray', 'yellow', 'darkpurple', 'lightgray'
]

# Create a map centered at the central point in Bengaluru
central_point = [center_lat, center_lon]
m = folium.Map(location=central_point, tiles="cartodbpositron", zoom_start=14)

# Plot the central point with a distinctive marker
folium.Marker(
    location=central_point,
    popup="Central Point (Bengaluru)",
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Add markers for each point with color based on its cluster
for i, (coord, label) in enumerate(zip(points_array, labels)):
    color = colors[label % len(colors)] if label != -1 else 'black'  # Noise points in black
    folium.CircleMarker(
        location=[coord[0], coord[1]],
        radius=3,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.6,
        popup=f"Cluster {label}<br>Lat: {coord[0]:.6f}, Long: {coord[1]:.6f}"
    ).add_to(m)

# Display the map
m
